In [1]:
import os
import shutil
import pandas as pd
import mercury as mr
from supervised.automl import AutoML 

In [2]:
from typing import List

In [3]:
import warnings
warnings.filterwarnings("ignore")

In [4]:
app = mr.App(title="Train AutoML 🧑‍💻", description="Train ML pipeline with MLJAR AutoML")

mercury.App

# Train Machine Learning Pipeline with MLJAR AutoML
Please follow the steps:
1. Upload CSV file with data. Data should heave column names in the first line.
2. Select input features and target column.
3. Select AutoML training mode, algorithms and training time limit.
4. Directory with all ML models will be zipped and available to download.

In [5]:
# data_file = mr.File(label="Upload CSV with training data", max_file_size="1MB")

In [6]:
# if data_file.filepath is None:
#     mr.Stop()

In [7]:
# df = pd.read_csv(data_file.filepath)

In [40]:
from sklearn.datasets import load_iris
df = load_iris(return_X_y = True, as_frame = True)

In [41]:
mr.Markdown("### Training data")

### Training data

In [42]:
df

(     sepal length (cm)  sepal width (cm)  petal length (cm)  petal width (cm)
 0                  5.1               3.5                1.4               0.2
 1                  4.9               3.0                1.4               0.2
 2                  4.7               3.2                1.3               0.2
 3                  4.6               3.1                1.5               0.2
 4                  5.0               3.6                1.4               0.2
 ..                 ...               ...                ...               ...
 145                6.7               3.0                5.2               2.3
 146                6.3               2.5                5.0               1.9
 147                6.5               3.0                5.2               2.0
 148                6.2               3.4                5.4               2.3
 149                5.9               3.0                5.1               1.8
 
 [150 rows x 4 columns],
 0      0
 1      0
 2   

In [43]:
df[0]

sepal length (cm)  sepal width (cm)  petal length (cm)  petal width (cm)
0                  5.1               3.5                1.4               0.2
1                  4.9               3.0                1.4               0.2
2                  4.7               3.2                1.3               0.2
3                  4.6               3.1                1.5               0.2
4                  5.0               3.6                1.4               0.2
..                 ...               ...                ...               ...
145                6.7               3.0                5.2               2.3
146                6.3               2.5                5.0               1.9
147                6.5               3.0                5.2               2.0
148                6.2               3.4                5.4               2.3
149                5.9               3.0                5.1               1.8

[150 rows x 4 columns]

In [44]:
df

(     sepal length (cm)  sepal width (cm)  petal length (cm)  petal width (cm)
 0                  5.1               3.5                1.4               0.2
 1                  4.9               3.0                1.4               0.2
 2                  4.7               3.2                1.3               0.2
 3                  4.6               3.1                1.5               0.2
 4                  5.0               3.6                1.4               0.2
 ..                 ...               ...                ...               ...
 145                6.7               3.0                5.2               2.3
 146                6.3               2.5                5.0               1.9
 147                6.5               3.0                5.2               2.0
 148                6.2               3.4                5.4               2.3
 149                5.9               3.0                5.1               1.8
 
 [150 rows x 4 columns],
 0      0
 1      0
 2   

In [45]:
x_columns = mr.MultiSelect(label="Input features", value=list(df[0].columns)[:-1], 
                           choices=list(df[0].columns))

mercury.MultiSelect

In [46]:
y_column = mr.Select(label="Target", value=list(df[0].columns)[-1], choices=list(df[0].columns))

mercury.Select

In [47]:
if x_columns.value is None or len(x_columns.value) == 0 or y_column.value is None:
    print("Please select input features and target column")
    mr.Stop()

In [68]:
mode = mr.Select(label="AutoML Mode", value="Explain", choices=["Explain", "Perform", "Compete"])

mercury.Select

In [49]:
algos = {
    "Explain": ["Baseline", "Linear", "Decision Tree", "Random Forest", "Xgboost", "Neural Network"],
    "Perform": ["Linear", "Random Forest", "LightGBM", "Xgboost", "CatBoost", "Neural Network"],
    "Compete": ["Decision Tree", "Random Forest", "Extra Trees", "LightGBM", 
                "Xgboost", "CatBoost", "Neural Network", "Nearest Neighbors"]
}

In [18]:
algorithms = mr.MultiSelect(label="Algorithms", value=algos[mode.value], choices=algos[mode.value])

mercury.MultiSelect

In [50]:
time_limit = mr.Select(label="Time limit (seconds)", value="60", choices=["60", "120", "240", "300"])

mercury.Select

In [69]:
start_training = mr.Button(label="Start training", style="success")

mercury.Button

In [52]:
output_dir = mr.OutputDir()

mercury.OutputDir

In [70]:
automl = AutoML(mode=mode.value, algorithms=algorithms.value,
                total_time_limit=int(time_limit.value))

In [54]:
x_columns.value

['sepal length (cm)', 'sepal width (cm)', 'petal length (cm)']

In [71]:
if start_training.clicked:
    mr.Markdown("### AutoML training logs")
    automl.fit(df[0][x_columns.value], df[0][y_column.value])
    
    output_filename = os.path.join(output_dir.path, automl._results_path)
    shutil.make_archive(output_filename, 'zip', automl._results_path)

### AutoML training logs

AutoML directory: AutoML_4
The task is regression with evaluation metric rmse
AutoML will use algorithms: ['Baseline', 'Linear', 'Decision Tree', 'Random Forest', 'Xgboost', 'Neural Network']
AutoML will stack models
AutoML will ensemble available models
AutoML steps: ['adjust_validation', 'simple_algorithms', 'default_algorithms', 'not_so_random', 'golden_features', 'kmeans_features', 'insert_random_feature', 'features_selection', 'hill_climbing_1', 'hill_climbing_2', 'boost_on_errors', 'ensemble', 'stack', 'ensemble_stacked']
* Step adjust_validation will try to check up to 1 model
1_DecisionTree rmse 0.17655 trained in 0.34 seconds
Disable stacking for split validation
* Step simple_algorithms will try to check up to 4 models
2_Baseline rmse 0.705007 trained in 0.35 seconds
3_DecisionTree rmse 0.169124 trained in 0.36 seconds
4_DecisionTree rmse 0.169124 trained in 0.35 seconds
5_Linear rmse 0.185766 trained in 0.36 seconds
* Step default_algorithms will try to check up to 3 models


In [72]:
automl

AutoML(algorithms=['Baseline', 'Linear', 'Decision Tree', 'Random Forest',
                   'Xgboost', 'Neural Network'],
       mode='Compete', total_time_limit=120)

In [73]:
automl._best_model

In [74]:
print(automl._best_model)

In [75]:
if automl._best_model is None:
    mr.Stop()

In [76]:
automl.report()